This notebook allows collecting results across multiple pipeline runs. Concatenating across sessions and bin sizes. 
It takes CSVs, then determines the most recent one from the filename. 

There are two major sets of decoded epochs - Laps and Ripples/Replays
There are two sets of marginals for the decoded epochs - the "by epoch" and "by time bin" marginals.
The "by time bin" epochs are a larger granulation, with each epoch consisting of one or more time bin.


```python

# 2024-01-23 - 
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-fet11-01_12-58-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-03_12-3-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_17-46-44_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-11-02_19-28-0_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-58-3_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-10_12-25-50_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_16-40-54_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_22-24-40_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_16-53-46_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-4-09_17-29-30_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_14-26-15_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-09_1-22-43_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-07_16-40-19_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-08_21-16-25_time_bin_size_sweep_results.h5
# C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-23_GL-2006-6-12_15-55-31_time_bin_size_sweep_results.h5



# found_session_export_paths = [Path(v).resolve() for v in  ["C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0420PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0645PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(laps_marginals_df).csv",
# "C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs/2024-01-12_0828PM-kdiba_pin01_one_fet11-01_12-58-54-(ripple_marginals_df).csv",
# ]]

[
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-17_0210AM-kdiba_vvp01_one_2006-4-09_17-29-30-(laps_simple_pf_pearson_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(laps_weighted_corr_merged_df)_tbin-0.025.csv",
    "2024-02-19_0430PM-kdiba_vvp01_one_2006-4-10_12-25-50-(ripple_weighted_corr_merged_df)_tbin-0.025.csv",
]

```

In [1]:
%config IPCompleter.use_jedi = False
%pdb off
%load_ext autoreload
%autoreload 3

# required to enable non-blocking interaction:
%gui qt5

import sys
from copy import deepcopy
from typing import Dict, List, Tuple, Optional, Callable, Union, Any
from typing_extensions import TypeAlias
from nptyping import NDArray
import neuropy.utils.type_aliases as types
from collections import defaultdict

import numpy as np
import pandas as pd
import re
from pathlib import Path
from datetime import datetime

from neuropy.utils.indexing_helpers import PandasHelpers
from pyphocorehelpers.indexing_helpers import partition_df
# Set the maximum number of columns to display
pd.set_option('display.max_columns', 100)

# Plotting
# import pylustrator # customization of figures
import matplotlib
import matplotlib as mpl
import matplotlib.pyplot as plt
_bak_rcParams = mpl.rcParams.copy()

matplotlib.use('Qt5Agg')
# %matplotlib inline
# %matplotlib auto

# Switch to the desired interactivity mode
plt.interactive(True)

# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
# _restore_previous_matplotlib_settings_callback = matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
import seaborn as sns

import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import plotly.io as pio
template: str = 'plotly_dark' # set plotl template
pio.templates.default = template
from pyphocorehelpers.plotting.media_output_helpers import fig_to_clipboard

from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _helper_build_figure, plotly_pre_post_delta_scatter, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# from ..PendingNotebookCode import plot_across_sessions_scatter_results, plot_histograms, plot_stacked_histograms
from pyphocorehelpers.Filesystem.path_helpers import find_first_extant_path
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import find_csv_files, find_HDF5_files, find_most_recent_files, process_csv_file, plot_across_sessions_scatter_results, plot_histograms, plot_stacked_histograms
from pyphoplacecellanalysis.General.Pipeline.Stages.ComputationFunctions.MultiContextComputationFunctions.DirectionalPlacefieldGlobalComputationFunctions import DecoderDecodedEpochsResult


debug_print: bool = False

# TODAY_DAY_DATE: str = f"2024-04-09_GL"
TODAY_DAY_DATE: str = f"2024-04-10_APOGEE"

print(f'TODAY_DAY_DATE: {TODAY_DAY_DATE}')

types.session_str: TypeAlias = str # a unique session identifier

def process_and_load_file(session_dict, df_file_name_key: str, loaded_dict: Dict, session_name: str, curr_session_t_delta: float, time_key: str) -> None:
    """ updates loaded_dict """
    try:
        file_path = session_dict[df_file_name_key]
        loaded_dict[session_name] = process_csv_file(file_path, session_name, curr_session_t_delta, time_key)
    except BaseException as e:
        print(f'session {session_name}, df_file_name_key: {df_file_name_key} - did not fully work. (error {e}. Skipping.')

def _common_cleanup_operations(a_df):
    """ post loading and concatenation across sessions dataframe cleanup """
    if a_df is None:
        return None
    ## Drop the weird 'Unnamed: 0' column:
    # Rename column 'Unnamed: 0' to 'abs_time_bin_index'
    a_df = a_df.rename(columns={'Unnamed: 0': 'abs_time_bin_index'})
    # Drop column: 'abs_time_bin_index'
    a_df = a_df.drop(columns=['abs_time_bin_index'])
    # Add additional 'epoch_idx' column for compatibility:
    if 'epoch_idx' not in a_df:
        if 'lap_idx' in a_df:
            a_df['epoch_idx'] = a_df['lap_idx']
        if 'ripple_idx' in a_df:
            a_df['epoch_idx'] = a_df['ripple_idx']
    return a_df

Automatic pdb calling has been turned OFF
build_module_logger(module_name="Spike3D.pipeline"):
	 Module logger com.PhoHale.Spike3D.pipeline has file logging enabled and will log to EXTERNAL\TESTING\Logging\debug_com.PhoHale.Spike3D.pipeline.log
TODAY_DAY_DATE: 2024-04-10_APOGEE


# Definitions
"_new" (as in `all_sessions_new_ripple_df`) adds simple_pearson and a few other measures

In [2]:
## Load across session t_delta CSV, which contains the t_delta for each session:

# cuttoff_date = datetime(2024, 3, 16)
cuttoff_date = None

# t_delta_csv_path = Path(r'C:\Users\pho\repos\Spike3DWorkEnv\Spike3D\output\collected_outputs\2024-01-18_GL_t_split_df.csv').resolve() # Apogee
# t_delta_csv_path = Path('/home/halechr/cloud/turbo/Data/Output/collected_outputs/2024-01-18_GL_t_split_df.csv').resolve() # GL

# collected_outputs_directory = '/home/halechr/FastData/collected_outputs/'
# collected_outputs_directory = r'C:\Users\pho\Desktop\collected_outputs'
# collected_outputs_directory = r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs' # APOGEE
# collected_outputs_directory = '/home/halechr/cloud/turbo/Data/Output/collected_outputs' # GL

known_collected_outputs_paths = [Path(v).resolve() for v in ['/Users/pho/Dropbox (University of Michigan)/MED-DibaLabDropbox/Data/Pho/Outputs/output/collected_outputs', r"K:/scratch/collected_outputs", r'C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/collected_outputs',
                                                              '/home/halechr/FastData/collected_outputs/', '/home/halechr/cloud/turbo/Data/Output/collected_outputs']]
collected_outputs_directory = find_first_extant_path(known_collected_outputs_paths)
assert collected_outputs_directory.exists(), f"collected_outputs_directory: {collected_outputs_directory} does not exist! Is the right computer's config commented out above?"
# fullwidth_path_widget(scripts_output_path, file_name_label='Scripts Output Path:')
print(f'collected_outputs_directory: {collected_outputs_directory}')

t_delta_csv_path = collected_outputs_directory.joinpath('2024-01-18_GL_t_split_df.csv').resolve() # GL
assert t_delta_csv_path.exists()

## Find the files:
csv_files = find_csv_files(collected_outputs_directory)
h5_files = find_HDF5_files(collected_outputs_directory)

csv_sessions = find_most_recent_files(found_session_export_paths=csv_files, cuttoff_date=cuttoff_date)
h5_sessions = find_most_recent_files(found_session_export_paths=h5_files)

## The CSV containing the session delta time:
t_delta_df = pd.read_csv(t_delta_csv_path, index_col=0) # Assuming that your CSV file has an index column
# adds `delta_aligned_t_start`, `delta_aligned_t_end` columns
t_delta_df['delta_aligned_t_start'] = t_delta_df['t_start'] - t_delta_df['t_delta']
t_delta_df['delta_aligned_t_end'] = t_delta_df['t_end'] - t_delta_df['t_delta']

# computes `earliest_delta_aligned_t_start`, latest_delta_aligned_t_end
earliest_delta_aligned_t_start: float = np.nanmin(t_delta_df['delta_aligned_t_start'])
latest_delta_aligned_t_end: float = np.nanmax(t_delta_df['delta_aligned_t_end'])
print(f'earliest_delta_aligned_t_start: {earliest_delta_aligned_t_start}, latest_delta_aligned_t_end: {latest_delta_aligned_t_end}')
t_delta_dict = t_delta_df.to_dict(orient='index')
# t_delta_df

# #TODO 2024-03-02 12:12: - [ ] Could add weighted correlation if there is a dataframe for that and it's computed:
_df_raw_variable_names = ['simple_pf_pearson_merged_df', 'weighted_corr_merged_df']
_df_variables_names = ['laps_weighted_corr_merged_df', 'ripple_weighted_corr_merged_df', 'laps_simple_pf_pearson_merged_df', 'ripple_simple_pf_pearson_merged_df']

# # tbin_values_dict = {'laps': self.laps_decoding_time_bin_size, 'ripple': self.ripple_decoding_time_bin_size}
time_col_name_dict = {'laps': 'lap_start_t', 'ripple': 'ripple_start_t'} ## default should be 't_bin_center'

# fold older files:
# {'laps_marginals_df': 'lap_start_t', 'ripple_marginals_df': 'ripple_start_t', 'laps_time_bin_marginals_df':'t_bin_center', 'ripple_time_bin_marginals_df':'t_bin_center'}
    

# csv_sessions
# Extract each of the separate files from the sessions:

# final_sessions: Dict[types.session_str, Dict[str, Path]] = {}

final_sessions_loaded_laps_dict = {}
final_sessions_loaded_ripple_dict = {}
final_sessions_loaded_laps_time_bin_dict = {}
final_sessions_loaded_ripple_time_bin_dict = {}

final_sessions_loaded_simple_pearson_laps_dict = {}
final_sessions_loaded_simple_pearson_ripple_dict = {}

# stupid reudndant but compatible method
final_sessions_loaded_laps_wcorr_dict = {}
final_sessions_loaded_ripple_wcorr_dict = {}

final_sessions_loaded_laps_all_scores_dict = {}
final_sessions_loaded_ripple_all_scores_dict = {}

if cuttoff_date is not None:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if (an_export_datetime >= cuttoff_date)}
                                                                                              for session_str, session_dict in csv_sessions.items() }
else:
    # no cutoff recency date:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items()}
                                                                                            for session_str, session_dict in csv_sessions.items()}


for session_str, session_dict in final_sessions.items():
    session_name = str(session_str)  # Extract session name from the filename
    if debug_print:
        print(f'processing session_name: {session_name}')
    curr_session_t_delta = t_delta_dict.get(session_name, {}).get('t_delta', None)
    if curr_session_t_delta is None:
        print(f'WARN: curr_session_t_delta is None for session_str = "{session_str}"')

    # Process each file type with its corresponding details
    process_and_load_file(session_dict, 'laps_marginals_df', final_sessions_loaded_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_marginals_df', final_sessions_loaded_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    process_and_load_file(session_dict, 'laps_time_bin_marginals_df', final_sessions_loaded_laps_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    process_and_load_file(session_dict, 'ripple_time_bin_marginals_df', final_sessions_loaded_ripple_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    process_and_load_file(session_dict, 'laps_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    process_and_load_file(session_dict, 'laps_weighted_corr_merged_df', final_sessions_loaded_laps_wcorr_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_weighted_corr_merged_df', final_sessions_loaded_ripple_wcorr_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    
    # process_and_load_file(session_dict, 'laps_all_scores_merged_df', final_sessions_loaded_laps_all_scores_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_all_scores_merged_df', final_sessions_loaded_ripple_all_scores_dict, session_str, curr_session_t_delta, 'ripple_start_t')



## Build across_sessions join dataframes:
all_sessions_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_dict.values()), axis='index', ignore_index=True)
all_sessions_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_dict.values()), axis='index', ignore_index=True)
# Add 'epoch_idx' column for compatibility:
if all_sessions_laps_df is not None:
    all_sessions_laps_df['epoch_idx'] = all_sessions_laps_df['lap_idx']
if all_sessions_ripple_df is not None:
    all_sessions_ripple_df['epoch_idx'] = all_sessions_ripple_df['ripple_idx']

# *_time_bin marginals:
all_sessions_laps_time_bin_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_time_bin_dict.values()), axis='index', ignore_index=True)
all_sessions_ripple_time_bin_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_time_bin_dict.values()), axis='index', ignore_index=True)

# NEW ________________________________________________________________________________________________________________ #
all_sessions_simple_pearson_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_simple_pearson_laps_dict.values()), axis='index', ignore_index=True)
all_sessions_simple_pearson_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_simple_pearson_ripple_dict.values()), axis='index', ignore_index=True)

if len(final_sessions_loaded_laps_wcorr_dict) > 0:
    all_sessions_wcorr_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_wcorr_dict.values()), axis='index', ignore_index=True)
else:
    all_sessions_wcorr_laps_df = None # empty df would be better

all_sessions_wcorr_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_wcorr_dict.values()), axis='index', ignore_index=True)

# `*_all_scores_*`: __________________________________________________________________________________________________ #
# all_sessions_all_score_laps_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_laps_all_scores_dict.values()), axis='index', ignore_index=True)
all_sessions_all_scores_ripple_df: pd.DataFrame = PandasHelpers.safe_concat(list(final_sessions_loaded_ripple_all_scores_dict.values()), axis='index', ignore_index=True)


dfs_list = (all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df)
for a_df in dfs_list:
    if a_df is not None:
        if 'time_bin_size' not in a_df:
            print('Uh-oh! time_bin_size is missing! This must be old exports!')
            print(f'\tTry to determine the time_bin_size from the filenames: {csv_sessions}')
            ## manual correction UwU
            time_bin_size: float = 0.025
            print(f'WARNING! MANUAL OVERRIDE TIME BIN SIZE SET: time_bin_size = {time_bin_size}. Assigning to dataframes....')
            a_df['time_bin_size'] = time_bin_size
        else:
            # Filter rows based on column: 'time_bin_size'
            a_df = a_df[a_df['time_bin_size'].notna()]


# if 'time_bin_size' not in all_sessions_laps_df:
#     print('Uh-oh! time_bin_size is missing! This must be old exports!')
#     print(f'\tTry to determine the time_bin_size from the filenames: {csv_sessions}')
#     ## manual correction UwU
#     time_bin_size: float = 0.025
#     print(f'WARNING! MANUAL OVERRIDE TIME BIN SIZE SET: time_bin_size = {time_bin_size}. Assigning to dataframes....')
#     all_sessions_laps_df['time_bin_size'] = time_bin_size
#     all_sessions_ripple_df['time_bin_size'] = time_bin_size
#     all_sessions_laps_time_bin_df['time_bin_size'] = time_bin_size
#     all_sessions_ripple_time_bin_df['time_bin_size'] = time_bin_size
#     print(f'\tdone.')
# else:
#     # Filter rows based on column: 'time_bin_size'
#     all_sessions_laps_df = all_sessions_laps_df[all_sessions_laps_df['time_bin_size'].notna()]
#     all_sessions_ripple_df = all_sessions_ripple_df[all_sessions_ripple_df['time_bin_size'].notna()]
#     all_sessions_laps_time_bin_df = all_sessions_laps_time_bin_df[all_sessions_laps_time_bin_df['time_bin_size'].notna()]
#     all_sessions_ripple_time_bin_df = all_sessions_ripple_time_bin_df[all_sessions_ripple_time_bin_df['time_bin_size'].notna()]

all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_laps_df, all_sessions_ripple_df, all_sessions_laps_time_bin_df, all_sessions_ripple_time_bin_df)]
all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_simple_pearson_laps_df, all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_laps_df, all_sessions_wcorr_ripple_df)]

# all_sessions_all_score_laps_df, all_sessions_all_scores_ripple_df = [_common_cleanup_operations(a_df) for a_df in (all_sessions_all_score_laps_df, all_sessions_all_scores_ripple_df)]
# all_sessions_all_score_laps_df = _common_cleanup_operations(all_sessions_all_score_laps_df)
all_sessions_all_scores_ripple_df = _common_cleanup_operations(all_sessions_all_scores_ripple_df)

all_sessions_simple_pearson_laps_df: pd.DataFrame = DecoderDecodedEpochsResult.merge_decoded_epochs_result_dfs(all_sessions_simple_pearson_laps_df, all_sessions_wcorr_laps_df, should_drop_directional_columns=False, start_t_idx_name='delta_aligned_start_t')
all_sessions_simple_pearson_ripple_df: pd.DataFrame = DecoderDecodedEpochsResult.merge_decoded_epochs_result_dfs(all_sessions_simple_pearson_ripple_df, all_sessions_wcorr_ripple_df, should_drop_directional_columns=False, start_t_idx_name='ripple_start_t')

# all_sessions_laps_time_bin_df # 601845 rows × 9 column

collected_outputs_directory: K:\scratch\collected_outputs
ERR: Could not parse filename: "session_h5_files_copydict_2024-03-28_Apogee"
earliest_delta_aligned_t_start: -2057.2259484970764, latest_delta_aligned_t_end: 1661.8560019930592
WARN: curr_session_t_delta is None for session_str = "2006-6-12_15-55-31"
session 2006-6-12_15-55-31, df_file_name_key: laps_marginals_df - did not fully work. (error 'laps_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: ripple_marginals_df - did not fully work. (error 'ripple_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: laps_time_bin_marginals_df - did not fully work. (error 'laps_time_bin_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: ripple_time_bin_marginals_df - did not fully work. (error 'ripple_time_bin_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: laps_simple_pf_pearson_merged_df - did not fully work. (error 'laps_simple_pf_pearson_merged_df'. Skippin

In [ ]:
csv_sessions

In [5]:
h5_files

if cuttoff_date is not None:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items() if (an_export_datetime >= cuttoff_date)}
                                                                                              for session_str, session_dict in csv_sessions.items() }
else:
    # no cutoff recency date:
    final_sessions: Dict[types.session_str, Dict[str, Path]] = {session_str:{file_type:a_path for file_type, (a_path, an_decoding_time_bin_size_str, an_export_datetime) in session_dict.items()}
                                                                                            for session_str, session_dict in csv_sessions.items()}


for session_str, session_dict in final_sessions.items():
    session_name = str(session_str)  # Extract session name from the filename
    if debug_print:
        print(f'processing session_name: {session_name}')
    curr_session_t_delta = t_delta_dict.get(session_name, {}).get('t_delta', None)
    if curr_session_t_delta is None:
        print(f'WARN: curr_session_t_delta is None for session_str = "{session_str}"')

    # Process each file type with its corresponding details
    process_and_load_file(session_dict, 'laps_marginals_df', final_sessions_loaded_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_marginals_df', final_sessions_loaded_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    process_and_load_file(session_dict, 'laps_time_bin_marginals_df', final_sessions_loaded_laps_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    process_and_load_file(session_dict, 'ripple_time_bin_marginals_df', final_sessions_loaded_ripple_time_bin_dict, session_str, curr_session_t_delta, 't_bin_center')
    process_and_load_file(session_dict, 'laps_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_laps_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_simple_pf_pearson_merged_df', final_sessions_loaded_simple_pearson_ripple_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    process_and_load_file(session_dict, 'laps_weighted_corr_merged_df', final_sessions_loaded_laps_wcorr_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_weighted_corr_merged_df', final_sessions_loaded_ripple_wcorr_dict, session_str, curr_session_t_delta, 'ripple_start_t')
    
    # process_and_load_file(session_dict, 'laps_all_scores_merged_df', final_sessions_loaded_laps_all_scores_dict, session_str, curr_session_t_delta, 'lap_start_t')
    process_and_load_file(session_dict, 'ripple_all_scores_merged_df', final_sessions_loaded_ripple_all_scores_dict, session_str, curr_session_t_delta, 'ripple_start_t')




WARN: curr_session_t_delta is None for session_str = "2006-6-12_15-55-31"
session 2006-6-12_15-55-31, df_file_name_key: laps_marginals_df - did not fully work. (error 'laps_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: ripple_marginals_df - did not fully work. (error 'ripple_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: laps_time_bin_marginals_df - did not fully work. (error 'laps_time_bin_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: ripple_time_bin_marginals_df - did not fully work. (error 'ripple_time_bin_marginals_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: laps_simple_pf_pearson_merged_df - did not fully work. (error 'laps_simple_pf_pearson_merged_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: ripple_simple_pf_pearson_merged_df - did not fully work. (error 'ripple_simple_pf_pearson_merged_df'. Skipping.
session 2006-6-12_15-55-31, df_file_name_key: laps_weighted_corr_merged_df

In [ ]:
2024-03-28_Apogee_11-02_17-46-44_pipeline_results.h5

In [ ]:
h5_sessions # get 'pipeline_results' results
h5_sessions

[a_session_dict.get('pipeline_results', None)[0] for a_sess_name, a_session_dict in h5_sessions.items()]

In [ ]:


h5_session_names = list(h5_sessions.keys())
h5_session_names

In [ ]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import parse_filename




# _test_h5_filename = Path("2024-03-28_Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")
_test_h5_filename = Path("2024-03-28-Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")

parse_filename(_test_h5_filename)

In [6]:
# _test_h5_filename = Path("2024-03-28-Apogee_kdiba_gor01_one_2006-6-08_14-26-15_pipeline_results.h5")
_test_h5_filename = Path("2024-03-28_Apogee_11-02_17-46-44_pipeline_results.h5")

basename: str = _test_h5_filename.stem
final_parsed_output_dict = try_parse_chain(basename=basename)
final_parsed_output_dict
# a_test_parser = DayDateOnlyParser()
# a_test_parser.try_parse(_test_h5_filename.stem)

NameError: name 'try_parse_chain' is not defined

In [ ]:
from pyphocorehelpers.Filesystem.path_helpers import read_filelist_from_text_file

an_h5_filelist_path = Path(r'L:/Scratch/collected_outputs/2024-03-28_Apogee_all_sessions_h5_filelist.txt').resolve()
read_hdf5_output_paths = read_filelist_from_text_file(filelist_path=an_h5_filelist_path, debug_print=False)
read_hdf5_output_paths

In [8]:
from neuropy.core.user_annotations import UserAnnotationsManager

## INPUTS: h5_sessions
h5_session_names = list(h5_sessions.keys())
good_sessions = UserAnnotationsManager.get_hardcoded_good_sessions()
h5_session_contexts = [a_good_session_ctxt for a_good_session_ctxt in good_sessions if (a_good_session_ctxt.session_name in h5_session_names)]
h5_session_contexts

# included_h5_paths = [a_session_dict.get('pipeline_results', None)[0] for a_sess_name, a_session_dict in h5_sessions.items()] # these are mis-ordered
included_h5_paths = [h5_sessions[a_good_session_ctxt.session_name].get('pipeline_results', None)[0] for a_good_session_ctxt in h5_session_contexts]
assert len(included_h5_paths) == len(h5_session_contexts)

h5_contexts_paths_dict = dict(zip(h5_session_contexts, included_h5_paths))
h5_contexts_paths_dict

{Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-08_14-26-15'): WindowsPath('K:/scratch/collected_outputs/2024-03-28_Apogee_2006-6-08_14-26-15_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-09_1-22-43'): WindowsPath('K:/scratch/collected_outputs/2024-03-28_Apogee_2006-6-09_1-22-43_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'one'
         session_name: '2006-6-12_15-55-31'): WindowsPath('K:/scratch/collected_outputs/2024-03-28_Apogee_2006-6-12_15-55-31_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'two'
         session_name: '2006-6-07_16-40-19'): WindowsPath('K:/scratch/collected_outputs/2024-03-28_Apogee_2006-6-07_16-40-19_pipeline_results.h5'),
 Context(format_name: 'kdiba'
         animal: 'gor01'
         exper_name: 'two'


In [9]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations

included_session_contexts = deepcopy(h5_session_contexts)
included_h5_paths = deepcopy(included_h5_paths)
num_sessions = len(included_session_contexts)
# neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)

neuron_replay_stats_table = AcrossSessionTables.build_neuron_replay_stats_table(included_session_contexts, included_h5_paths)
neuron_replay_stats_table

long_short_fr_indicies_analysis_table = AcrossSessionTables.build_long_short_fr_indicies_analysis_table(included_session_contexts, included_h5_paths)
long_short_fr_indicies_analysis_table


failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-12_16-53-46_pipeline_results.h5, table_key: /kdiba/gor01/two/2006-6-12_16-53-46/global_computations/jonathan_fr_analysis/neuron_replay_stats_df/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/two/2006-6-12_16-53-46/global_computations/jonathan_fr_analysis/neuron_replay_stats_df/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-4-10_12-58-3_pipeline_results.h5, table_key: /kdiba/vvp01/two/2006-4-10_12-58-3/global_computations/jonathan_fr_analysis/neuron_replay_stats_df/table. wth exception group ``/`` does not have a child named ``/kdiba/vvp01/two/2006-4-10_12-58-3/global_computations/jonathan_fr_analysis/neuron_replay_stats_df/table``. Skipping.
concatenating dataframes from 13 of 15 files
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-12_16-53-46_pipeline_results.h5, table_key: /kdiba/gor01/two/2006-6-12_16-53-4

format_name animal exper_name        session_name  index  \
0         kdiba  gor01        one  2006-6-08_14-26-15      0   
1         kdiba  gor01        one  2006-6-08_14-26-15      1   
2         kdiba  gor01        one  2006-6-08_14-26-15      2   
3         kdiba  gor01        one  2006-6-08_14-26-15      3   
4         kdiba  gor01        one  2006-6-08_14-26-15      4   
..          ...    ...        ...                 ...    ...   
777       kdiba  pin01        one   fet11-01_12-58-54     26   
778       kdiba  pin01        one   fet11-01_12-58-54     27   
779       kdiba  pin01        one   fet11-01_12-58-54     28   
780       kdiba  pin01        one   fet11-01_12-58-54     29   
781       kdiba  pin01        one   fet11-01_12-58-54     30   

                               neuron_uid                         session_uid  \
0    kdiba|gor01|one|2006-6-08_14-26-15|2  kdiba|gor01|one|2006-6-08_14-26-15   
1    kdiba|gor01|one|2006-6-08_14-26-15|3  kdiba|gor01|one|2006-6-08_14-26-15   
2    kdiba|gor01|one|2006-6-08_14-26-15|4  kdiba|gor01|one|2006-6-08_14-26-15   
3    kdiba|gor01|one|2006-6-08_14-26-15|5  kdiba|gor01|one|2006-6-08_14-26-15   
4    kdiba|gor01|one|2006-6-08_14-26-15|6  kdiba|gor01|one|2006-6-08_14-26-15   
..                                    ...                                 ...   
777  kdiba|pin01|one|fet11-01_12-58-54|28   kdiba|pin01|one|fet11-01_12-58-54   
778  kdiba|pin01|one|fet11-01_12-58-54|29   kdiba|pin01|one|fet11-01_12-58-54   
779  kdiba|pin01|one|fet11-01_12-58-54|30   kdiba|pin01|one|fet11-01_12-58-54   
780  kdiba|pin01|one|fet11-01_12-58-54|31   kdiba|pin01|one|fet11-01_12-58-54   
781  kdiba|pin01|one|fet11-01_12-58-54|32   kdiba|pin01|one|fet11-01_12-58-54   

     aclu  x_frs_index  y_frs_index    session_datetime  
0       2     0.950171     1.000000 2006-06-08 14:26:15  
1       3    -0.852388    -0.593507 2006-06-08 14:26:15  
2       4    -0.971940    -1.000000 2006-06-08 14:26:15  
3       5     0.147308    -0.043639 2006-06-08 14:26:15  
4       6     0.443550     0.445497 2006-06-08 14:26:15  
..    ...          ...          ...                 ...  
777    28    -0.557444     0.026565 2009-11-01 12:58:54  
778    29    -0.294036     0.247180 2009-11-01 12:58:54  
779    30    -0.249504     0.131576 2009-11-01 12:58:54  
780    31     0.256910     0.257815 2009-11-01 12:58:54  
781    32     0.507367     0.363465 2009-11-01 12:58:54  

[782 rows x 11 columns]

In [10]:
neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)
long_short_fr_indicies_analysis_table

failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-08_14-26-15_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-08_14-26-15/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-08_14-26-15/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-09_1-22-43_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-09_1-22-43/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-09_1-22-43/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-12_15-55-31_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-12_15-55-31/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-12_15-55-31/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006

format_name animal exper_name        session_name  index  \
0         kdiba  gor01        one  2006-6-08_14-26-15      0   
1         kdiba  gor01        one  2006-6-08_14-26-15      1   
2         kdiba  gor01        one  2006-6-08_14-26-15      2   
3         kdiba  gor01        one  2006-6-08_14-26-15      3   
4         kdiba  gor01        one  2006-6-08_14-26-15      4   
..          ...    ...        ...                 ...    ...   
777       kdiba  pin01        one   fet11-01_12-58-54     26   
778       kdiba  pin01        one   fet11-01_12-58-54     27   
779       kdiba  pin01        one   fet11-01_12-58-54     28   
780       kdiba  pin01        one   fet11-01_12-58-54     29   
781       kdiba  pin01        one   fet11-01_12-58-54     30   

                               neuron_uid                         session_uid  \
0    kdiba|gor01|one|2006-6-08_14-26-15|2  kdiba|gor01|one|2006-6-08_14-26-15   
1    kdiba|gor01|one|2006-6-08_14-26-15|3  kdiba|gor01|one|2006-6-08_14-26-15   
2    kdiba|gor01|one|2006-6-08_14-26-15|4  kdiba|gor01|one|2006-6-08_14-26-15   
3    kdiba|gor01|one|2006-6-08_14-26-15|5  kdiba|gor01|one|2006-6-08_14-26-15   
4    kdiba|gor01|one|2006-6-08_14-26-15|6  kdiba|gor01|one|2006-6-08_14-26-15   
..                                    ...                                 ...   
777  kdiba|pin01|one|fet11-01_12-58-54|28   kdiba|pin01|one|fet11-01_12-58-54   
778  kdiba|pin01|one|fet11-01_12-58-54|29   kdiba|pin01|one|fet11-01_12-58-54   
779  kdiba|pin01|one|fet11-01_12-58-54|30   kdiba|pin01|one|fet11-01_12-58-54   
780  kdiba|pin01|one|fet11-01_12-58-54|31   kdiba|pin01|one|fet11-01_12-58-54   
781  kdiba|pin01|one|fet11-01_12-58-54|32   kdiba|pin01|one|fet11-01_12-58-54   

     aclu  x_frs_index  y_frs_index    session_datetime  
0       2     0.950171     1.000000 2006-06-08 14:26:15  
1       3    -0.852388    -0.593507 2006-06-08 14:26:15  
2       4    -0.971940    -1.000000 2006-06-08 14:26:15  
3       5     0.147308    -0.043639 2006-06-08 14:26:15  
4       6     0.443550     0.445497 2006-06-08 14:26:15  
..    ...          ...          ...                 ...  
777    28    -0.557444     0.026565 2009-11-01 12:58:54  
778    29    -0.294036     0.247180 2009-11-01 12:58:54  
779    30    -0.249504     0.131576 2009-11-01 12:58:54  
780    31     0.256910     0.257815 2009-11-01 12:58:54  
781    32     0.507367     0.363465 2009-11-01 12:58:54  

[782 rows x 11 columns]

In [11]:
neuron_replay_stats_table

format_name animal exper_name        session_name  long_pf_peak_x  \
0         kdiba  gor01        one  2006-6-08_14-26-15      213.121619   
1         kdiba  gor01        one  2006-6-08_14-26-15      141.054181   
2         kdiba  gor01        one  2006-6-08_14-26-15      201.742550   
3         kdiba  gor01        one  2006-6-08_14-26-15      235.879758   
4         kdiba  gor01        one  2006-6-08_14-26-15             NaN   
..          ...    ...        ...                 ...             ...   
777       kdiba  pin01        one   fet11-01_12-58-54      132.353634   
778       kdiba  pin01        one   fet11-01_12-58-54       57.811368   
779       kdiba  pin01        one   fet11-01_12-58-54      121.172294   
780       kdiba  pin01        one   fet11-01_12-58-54      218.077239   
781       kdiba  pin01        one   fet11-01_12-58-54       65.265594   

     short_pf_peak_x track_membership  long_non_replay_mean  \
0                NaN        LEFT_ONLY              0.412424   
1         129.675112           SHARED              0.274069   
2         182.777435           SHARED              0.119382   
3         201.742550           SHARED              2.326046   
4                NaN           SHARED             25.389639   
..               ...              ...                   ...   
777       139.807860           SHARED              1.227517   
778       102.536727           SHARED              0.929991   
779       128.626520           SHARED              0.952187   
780       188.260333           SHARED              1.156581   
781        98.809614           SHARED              1.447410   

     short_non_replay_mean  non_replay_diff  long_replay_mean  \
0                 0.115533        -0.296891          7.912740   
1                 1.394595         1.120526          9.241991   
2                 0.924896         0.805514               NaN   
3                 2.012612        -0.313434         11.994904   
4                12.754636       -12.635004        105.811996   
..                     ...              ...               ...   
777               1.316956         0.089439          8.804707   
778               0.838893        -0.091098          8.640242   
779               0.842384        -0.109803          8.726043   
780               1.026152        -0.130429          6.526651   
781               0.454860        -0.992551         11.779994   

     short_replay_mean  replay_diff  long_mean  short_mean  mean_diff  \
0                  NaN          NaN   4.162582         NaN        NaN   
1             8.536258    -0.705733   4.758030    4.965426   0.207397   
2            12.484801          NaN        NaN    6.704848        NaN   
3            11.315249    -0.679655   7.160475    6.663930  -0.496545   
4            41.364962   -64.447034  65.600818   27.059799 -38.541019   
..                 ...          ...        ...         ...        ...   
777           9.155474     0.350768   5.016112    5.236215   0.220103   
778           8.106845    -0.533397   4.785116    4.472869  -0.312248   
779           7.650765    -1.075278   4.839115    4.246575  -0.592540   
780           6.448056    -0.078595   3.841616    3.737104  -0.104512   
781           9.450924    -2.329070   6.613702    4.952892  -1.660810   

     num_replays  long_num_replays  short_num_replays neuron_type  aclu  \
0             45                45                  0         pyr     2   
1             91                23                 68         pyr     3   
2             87                 0                 87         pyr     4   
3            229               126                103         pyr     5   
4            602               345                257        intr     6   
..           ...               ...                ...         ...   ...   
777          181               100                 81         pyr    28   
778          328               233                 95         pyr    29   
779          186               119   

In [13]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsResults

# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')

AcrossSessionsResults.post_compute_all_sessions_processing(global_data_root_parent_path=collected_outputs_directory, BATCH_DATE_TO_USE=TODAY_DAY_DATE, plotting_enabled=True)

global_batch_result_inst_fr_file_path: K:\scratch\collected_outputs\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-10_APOGEE.pkl
Loading loaded session pickle file results : K:\scratch\collected_outputs\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-10_APOGEE.pkl... done.


FileNotFoundError: [Errno 2] No such file or directory: 'K:\\scratch\\collected_outputs\\across_session_result_long_short_recomputed_inst_firing_rate_2024-04-10_APOGEE.pkl'

In [ ]:
global_multi_session_context, _out_aggregate_fig_2 = AcrossSessionsVisualizations.across_sessions_bar_graphs(across_session_inst_fr_computation, num_sessions, enable_tiny_point_labels=False, enable_hover_labels=False)

In [14]:
graphics_output_dict = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions)

register_output_file(output_path: C:\Users\pho\repos\Spike3DWorkEnv\Spike3D\SCRATCH\EXTERNAL\Screenshots\ProgrammaticDisplayFunctionTesting\2024-04-10\kdiba\15_display_long_short_laps.png, ...)
	 saved "file:///C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/SCRATCH/EXTERNAL/Screenshots/ProgrammaticDisplayFunctionTesting/2024-04-10/kdiba/15_display_long_short_laps.png"


In [ ]:
print(list(all_sessions_all_scores_ripple_df.columns)) # ['start', 'stop', 'label', 'duration', 'is_user_annotated_epoch', 'is_valid_epoch', 'P_LR', 'P_RL', 'P_Long', 'P_Short', 'P_Long_LR', 'score_long_LR', 'velocity_long_LR', 'intercept_long_LR', 'speed_long_LR', 'wcorr_long_LR', 'pearsonr_long_LR', 'travel_long_LR', 'coverage_long_LR', 'jump_long_LR', 'longest_sequence_length_ratio_long_LR', 'direction_change_bin_ratio_long_LR', 'congruent_dir_bins_ratio_long_LR', 'total_congruent_direction_change_long_LR', 'P_Long_RL', 'score_long_RL', 'velocity_long_RL', 'intercept_long_RL', 'speed_long_RL', 'wcorr_long_RL', 'pearsonr_long_RL', 'travel_long_RL', 'coverage_long_RL', 'jump_long_RL', 'longest_sequence_length_ratio_long_RL', 'direction_change_bin_ratio_long_RL', 'congruent_dir_bins_ratio_long_RL', 'total_congruent_direction_change_long_RL', 'P_Short_LR', 'score_short_LR', 'velocity_short_LR', 'intercept_short_LR', 'speed_short_LR', 'wcorr_short_LR', 'pearsonr_short_LR', 'travel_short_LR', 'coverage_short_LR', 'jump_short_LR', 'longest_sequence_length_ratio_short_LR', 'direction_change_bin_ratio_short_LR', 'congruent_dir_bins_ratio_short_LR', 'total_congruent_direction_change_short_LR', 'P_Short_RL', 'score_short_RL', 'velocity_short_RL', 'intercept_short_RL', 'speed_short_RL', 'wcorr_short_RL', 'pearsonr_short_RL', 'travel_short_RL', 'coverage_short_RL', 'jump_short_RL', 'longest_sequence_length_ratio_short_RL', 'direction_change_bin_ratio_short_RL', 'congruent_dir_bins_ratio_short_RL', 'total_congruent_direction_change_short_RL', 'ripple_start_t', 'long_best_travel', 'short_best_travel', 'travel_diff', 'long_best_coverage', 'short_best_coverage', 'coverage_diff', 'long_best_jump', 'short_best_jump', 'jump_diff', 'long_best_longest_sequence_length_ratio', 'short_best_longest_sequence_length_ratio', 'longest_sequence_length_ratio_diff', 'long_best_direction_change_bin_ratio', 'short_best_direction_change_bin_ratio', 'direction_change_bin_ratio_diff', 'long_best_congruent_dir_bins_ratio', 'short_best_congruent_dir_bins_ratio', 'congruent_dir_bins_ratio_diff', 'long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change', 'total_congruent_direction_change_diff', 'session_name', 'time_bin_size', 'delta_aligned_start_t']
# ['long_best_total_congruent_direction_change', 'short_best_total_congruent_direction_change']
['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']

In [ ]:
all_sessions_simple_pearson_ripple_df # 3138 rows × 24 columns

In [ ]:
all_sessions_simple_pearson_laps_df # 931 rows × 25 columns

In [ ]:
all_sessions_ripple_df # 17592 rows × 10 columns

In [ ]:
csv_files

In [15]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import export_across_session_CSVs

# TODAY_DAY_DATE: str = f"2024-03-18_Apogee"
final_output_path = Path("../output/").resolve()

final_csv_export_paths = export_across_session_CSVs(final_output_path=final_output_path, TODAY_DAY_DATE=TODAY_DAY_DATE,
                                                    all_sessions_laps_df=all_sessions_laps_df,  all_sessions_ripple_df=all_sessions_ripple_df,  all_sessions_laps_time_bin_df=all_sessions_laps_time_bin_df,  all_sessions_ripple_time_bin_df=all_sessions_ripple_time_bin_df, 
                                                    all_sessions_simple_pearson_laps_df=all_sessions_simple_pearson_laps_df,  all_sessions_simple_pearson_ripple_df=all_sessions_simple_pearson_ripple_df,
                                                    all_sessions_all_scores_ripple_df=all_sessions_all_scores_ripple_df,  all_sessions_all_scores_laps_df=None,
                                                    )
final_csv_export_paths

{'AcrossSession_Laps_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_Laps_per-Epoch.csv'),
 'AcrossSession_Ripple_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_Ripple_per-Epoch.csv'),
 'AcrossSession_Laps_per-TimeBin': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_Laps_per-TimeBin.csv'),
 'AcrossSession_Ripple_per-TimeBin': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_Ripple_per-TimeBin.csv'),
 'AcrossSession_SimplePearson_Laps_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_SimplePearson_Laps_per-Epoch.csv'),
 'AcrossSession_SimplePearson_Ripple_per-Epoch': WindowsPath('C:/Users/pho/repos/Spike3DWorkEnv/Spike3D/output/2024-04-10_APOGEE_AcrossSession_SimplePearson_Ripple_per-Epoch.csv'),
 'AcrossSession_AllScores_Ripp

In [16]:
all_sessions_all_scores_ripple_df

start         stop  label  duration  is_user_annotated_epoch  \
0        5.696837     5.758983      0  0.062147                    False   
1       27.174099    27.439336      1  0.265236                    False   
2       96.866562    97.257596      2  0.391035                    False   
3      121.201428   121.606901      3  0.405473                    False   
4      125.183137   125.292009      4  0.108872                    False   
...           ...          ...    ...       ...                      ...   
3861  2034.655153  2034.765468    629  0.110315                    False   
3862  2043.892191  2044.079430    630  0.187238                    False   
3863  2045.095432  2045.393262    631  0.297830                     True   
3864  2051.142292  2051.269043    632  0.126751                     True   
3865  2053.276532  2053.445093    633  0.168561                    False   

      is_valid_epoch      P_LR      P_RL    P_Long   P_Short  P_Long_LR  \
0               True  0.771442  0.228558  0.639360  0.360640   0.493229   
1              False  0.510945  0.489055  0.495263  0.504737   0.253052   
2               True  0.380731  0.619269  0.543552  0.456448   0.206947   
3              False  0.316117  0.683883  0.495285  0.504715   0.156568   
4               True  0.130706  0.869294  0.809296  0.190704   0.105780   
...              ...       ...       ...       ...       ...        ...   
3861            True  0.000316  0.999684  0.252939  0.747061   0.000080   
3862            True  0.430877  0.569123  0.606759  0.393241   0.261439   
3863            True  0.398701  0.601299  0.435845  0.564155   0.173772   
3864            True  0.013759  0.986241  0.161866  0.838134   0.002227   
3865            True  0.710155  0.289845  0.345384  0.654616   0.245276   

      score_long_LR  velocity_long_LR  intercept_long_LR  speed_long_LR  \
0          0.733209        682.863416         167.051151     682.863416   
1          0.338389         23.582867         182.711950      23.582867   
2          0.379806         11.124767         214.173480      11.124767   
3          0.473496         -5.215588          18.683737       5.215588   
4          0.896102        195.502151          10.252852     195.502151   
...             ...               ...                ...            ...   
3861       0.708434       -183.184319         211.204525     183.184319   
3862       0.592488        -98.459108          42.663808      98.459108   
3863       0.369658          9.184061          24.204262       9.184061   
3864       0.608333        735.918640         111.072891     735.918640   
3865       0.604485        691.310069          51.714159     691.310069   

      wcorr_long_LR  pearsonr_long_LR  travel_long_LR  coverage_long_LR  \
0          0.577784               NaN        0.035694          0.262295   
1          0.074217               NaN        0.186402          0.311475   
2          0.126189          0.254583        0.160623          0.426230   
3          0.104757               NaN        0.425949          0.311475   
4          0.469147               NaN        0.053541          0.213115   
...             ...               ...             ...               ...   
3861      -0.449720               NaN        0.100438          0.258065   
3862      -0.648317               NaN        0.153612          0.306452   
3863      -0.462515               NaN        0.255231          0.354839   
3864       0.527320          0.696053        0.155089          0.354839   
3865       0.620141               NaN        0.166609          0.274194   

      jump_long_LR  longest_sequence_length_ratio_long_LR  \
0         0.000156                               0.500000   
1         0.002025                               0.200000   
2         0.004128                               0.133333   
3         0.004673                               0.125000   
4         0.000467                               0.250000   
...            ...            

In [17]:

all_sessions_simple_pearson_ripple_df

P_LR      P_RL    P_Long   P_Short  ripple_idx  ripple_start_t  \
0     0.771442  0.228558  0.639360  0.360640           0        5.696837   
1     0.510945  0.489055  0.495263  0.504737           1       27.174099   
2     0.380731  0.619269  0.543552  0.456448           2       96.866562   
3     0.316117  0.683883  0.495285  0.504715           3      121.201428   
4     0.130706  0.869294  0.809296  0.190704           4      125.183137   
...        ...       ...       ...       ...         ...             ...   
4110  0.000316  0.999684  0.252939  0.747061         606     2034.655153   
4111  0.430877  0.569123  0.606759  0.393241         607     2043.892191   
4112  0.398701  0.601299  0.435845  0.564155         608     2045.095432   
4113  0.013759  0.986241  0.161866  0.838134         609     2051.142292   
4114  0.710155  0.289845  0.345384  0.654616         610     2053.276532   

      P_Long_LR  P_Long_RL  P_Short_LR  P_Short_RL  most_likely_decoder_index  \
0      0.493229   0.146131    0.278213    0.082427                          0   
1      0.253052   0.242211    0.257893    0.246844                          2   
2      0.206947   0.336605    0.173784    0.282664                          1   
3      0.156568   0.338717    0.159549    0.345166                          3   
4      0.105780   0.703516    0.024926    0.165778                          1   
...         ...        ...         ...         ...                        ...   
4110   0.000080   0.252859    0.000236    0.746825                          3   
4111   0.261439   0.345320    0.169439    0.223802                          1   
4112   0.173772   0.262073    0.224929    0.339226                          3   
4113   0.002227   0.159639    0.011532    0.826602                          3   
4114   0.245276   0.100108    0.464879    0.189737                          2   

            start         stop  label  duration  long_LR_pf_peak_x_pearsonr  \
0        5.696837     5.758983      0  0.062147                         NaN   
1       27.174099    27.439336      1  0.265236                         NaN   
2       96.866562    97.257596      2  0.391035                    0.254583   
3      121.201428   121.606901      3  0.405473                         NaN   
4      125.183137   125.292009      4  0.108872                         NaN   
...           ...          ...    ...       ...                         ...   
4110  2034.655153  2034.765468    629  0.110315                         NaN   
4111  2043.892191  2044.079430    630  0.187238                         NaN   
4112  2045.095432  2045.393262    631  0.297830                         NaN   
4113  2051.142292  2051.269043    632  0.126751                    0.696053   
4114  2053.276532  2053.445093    633  0.168561                         NaN   

      long_RL_pf_peak_x_pearsonr  short_LR_pf_peak_x_pearsonr  \
0                            NaN                          NaN   
1                            NaN                          NaN   
2                       0.070291                     0.153462   
3                      -0.079630                          NaN   
4                       0.510361                          NaN   
...                          ...                          ...   
4110                         NaN                          NaN   
4111                         NaN                          NaN   
4112                         NaN                          NaN   
4113                    0.724570                     0.690877   
4114                         NaN                          NaN   

      short_RL_pf_peak_x_pearsonr  best_decoder_index  \
0                             NaN                   0   
1                             NaN                   0   
2                        0.224289                   0   
3                        0.318755                   0   
4                        0.472233                   0   
...                           ...                 ..

In [18]:
## find all columns starting with 'wcorr': wcorr_long_LR
sub_string: str = 'wcorr'
sub_string: str = 'pearsonr'
columns_list = list(all_sessions_simple_pearson_ripple_df.columns)
matching_columns = [s for s in columns_list if sub_string in s]
print(matching_columns) # ['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

assert np.shape(all_sessions_simple_pearson_ripple_df)[0] == np.shape(all_sessions_all_scores_ripple_df)[0], f"np.shape(all_sessions_all_scores_ripple_df)[0]: {np.shape(all_sessions_all_scores_ripple_df)[0]} != np.shape(all_sessions_simple_pearson_ripple_df)[0]: {np.shape(all_sessions_simple_pearson_ripple_df)[0]}"



['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']


AssertionError: np.shape(all_sessions_all_scores_ripple_df)[0]: 3866 != np.shape(all_sessions_simple_pearson_ripple_df)[0]: 4115

In [19]:
['long_LR_pf_peak_x_pearsonr', 'long_RL_pf_peak_x_pearsonr', 'short_LR_pf_peak_x_pearsonr', 'short_RL_pf_peak_x_pearsonr', 'long_best_pf_peak_x_pearsonr', 'short_best_pf_peak_x_pearsonr', 'pearsonr_abs_diff']
['wcorr_long_LR', 'wcorr_long_RL', 'wcorr_short_LR', 'wcorr_short_RL', 'long_best_wcorr', 'short_best_wcorr', 'wcorr_abs_diff']

['wcorr_long_LR',
 'wcorr_long_RL',
 'wcorr_short_LR',
 'wcorr_short_RL',
 'long_best_wcorr',
 'short_best_wcorr',
 'wcorr_abs_diff']

# 2024-03-02 - Get only the user-annotated ripples:

In [20]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _split_user_annotated_ripple_df

## Bump
# input_df = all_sessions_simple_pearson_ripple_df
# input_df = all_sessions_all_scores_ripple_df

all_sessions_all_scores_ripple_df, (valid_ripple_df, invalid_ripple_df), (user_approved_ripple_df, user_approved_ripple_df) = _split_user_annotated_ripple_df(all_sessions_all_scores_ripple_df)

## 2024-03-14 - 'is_valid_epoch' column
# 'is_valid_epoch'
## OUTPUTS: valid_ripple_df, invalid_ripple_df, user_approved_ripple_df, user_rejected_ripple_df, (user_annotated_epoch_unique_session_names, unannotated_session_names)
user_approved_ripple_df

user_annotated_epoch_unique_session_names: ['kdiba_gor01_one_2006-6-12_15-55-31' 'kdiba_pin01_one_fet11-01_12-58-54'
 'kdiba_pin01_one_11-02_19-28-0' 'kdiba_pin01_one_11-02_17-46-44'
 'kdiba_gor01_two_2006-6-08_21-16-25' 'kdiba_gor01_two_2006-6-09_22-24-40'
 'kdiba_gor01_two_2006-6-07_16-40-19' 'kdiba_gor01_one_2006-6-09_1-22-43'
 'kdiba_gor01_one_2006-6-08_14-26-15']
unannotated_session_names: set()
n_input_df_rows: 3866
	 n_valid_df_rows: 2399
	 n_invalid_df_rows: 1467
n_input_df_rows: 2399
	 n_user_approved_df_rows: 415
	 n_user_rejected_df_rows: 1984


start         stop  label  duration      P_LR      P_RL    P_Long  \
0     127.872518   128.242295      6  0.369776  0.332359  0.667641  0.719677   
1     153.505672   153.850873     11  0.345200  0.242063  0.757937  0.722788   
2     165.036019   165.260244     12  0.224225  0.549536  0.450464  0.693093   
3     535.653829   535.812313     55  0.158484  0.170225  0.829775  0.848133   
4     540.199004   540.442306     57  0.243302  0.200525  0.799475  0.681276   
..           ...          ...    ...       ...       ...       ...       ...   
410  1925.050120  1925.228173    609  0.178053  0.124468  0.875532  0.385564   
411  1966.702763  1967.053063    615  0.350300  0.321770  0.678230  0.306304   
412  1998.452665  1998.565715    622  0.113050  0.999713  0.000287  0.553314   
413  2045.095432  2045.393262    631  0.297830  0.398701  0.601299  0.435845   
414  2051.142292  2051.269043    632  0.126751  0.013759  0.986241  0.161866   

      P_Short  P_Long_LR  score_long_LR  velocity_long_LR  intercept_long_LR  \
0    0.280323   0.239191       0.338934       -150.701907         212.526540   
1    0.277212   0.174960       0.384653         18.870274          15.551207   
2    0.306907   0.380879       0.494846        553.011642         178.641818   
3    0.151867   0.144373       0.564618        -16.578653          19.813078   
4    0.318724   0.136613       0.416463        -44.356668          27.607541   
..        ...        ...            ...               ...                ...   
410  0.614436   0.047990       0.612198       1088.196134           8.379368   
411  0.693696   0.098559       0.408742         -2.602396         219.498282   
412  0.446686   0.553155       0.718113       -578.443617         179.974877   
413  0.564155   0.173772       0.369658          9.184061          24.204262   
414  0.838134   0.002227       0.608333        735.918640         111.072891   

     speed_long_LR  wcorr_long_LR  pearsonr_long_LR  travel_long_LR  \
0       150.701907       0.059945         -0.294919        0.293789   
1        18.870274       0.291247               NaN        0.459560   
2       553.011642      -0.559428          0.634974        0.313597   
3        16.578653      -0.717555               NaN        0.260566   
4        44.356668      -0.396498               NaN        0.350248   
..             ...            ...               ...             ...   
410    1088.196134       0.865770               NaN        0.224509   
411       2.602396       0.012342         -0.091480        0.466288   
412     578.443617      -0.857533          0.411776        0.100438   
413       9.184061      -0.462515               NaN        0.255231   
414     735.918640       0.527320          0.696053        0.155089   

     coverage_long_LR  jump_long_LR  longest_sequence_length_ratio_long_LR  \
0            0.360656      0.004361                               0.214286   
1            0.327869      0.004283                               0.153846   
2            0.393443      0.004439                               0.250000   
3            0.245902      0.003894                               0.333333   
4            0.393443      0.003816                               0.222222   
..                ...           ...                                    ...   
410          0.419355      0.002834                               0.428571   
411          0.290323      0.004596                               0.142857   
412          0.290323      0.000843                               0.250000   
413          0.354839      0.004443                               0.181818   
414          0.354839      0.001302                               0.600000   

     direction_change_bin_ratio_long_LR  congruent_dir_bins_ratio_long_LR  \
0                              0.615385                          0.384615   
1                              0.666667                          0.500000   
2                              0.857143                          0.4

In [ ]:
user_approved_ripple_df

In [ ]:
[col.split('_long_LR') for col in list(user_approved_ripple_df.columns)]



In [ ]:
## order columns for reasonability
['long_best_coverage', 'short_best_coverage', 'coverage_diff']

['coverage_short_RL']

['_long_LR', '_long_RL', '_short_LR', '_short_RL']
['long_best_', 'short_best_']
['_diff']


# PandasHelpers.reordering_columns(


In [ ]:
## want to compare difference between user approved and user rejected ripples

user_approved_ripple_df
user_rejected_ripple_df
# OUTPUTS: all_sessions_user_annotated_ripple_df, user_approved_ripple_df, user_rejected_ripple_df

In [ ]:
## Want to test for differences between long/short among only user approved ripples:

0.025


In [ ]:
df: pd.DataFrame = deepcopy(all_sessions_user_annotated_ripple_df)

### 2024-02-29 - 4pm - Filter the events for those meeting wcorr criteria:


In [21]:
# df: pd.DataFrame = deepcopy(all_sessions_user_annotated_ripple_df)
df: pd.DataFrame = deepcopy(valid_ripple_df) # valid epochs, but not just those that the user approved
# df: pd.DataFrame = deepcopy(user_approved_ripple_df)

## INPUTS: df

min_wcorr_threshold: float = 0.33
min_wcorr_diff_threshold: float = 0.2

# is_included_large_wcorr_diff = np.any((df[['wcorr_abs_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_large_wcorr_diff = np.any((df[['wcorr_diff']].abs() > min_wcorr_diff_threshold), axis=1)
is_included_high_wcorr = np.any((df[['long_best_wcorr', 'short_best_wcorr']].abs() > min_wcorr_threshold), axis=1)

df = df[is_included_high_wcorr]
df

# wcorr_long_LR


start         stop  label  duration  is_user_annotated_epoch  \
0        5.696837     5.758983      0  0.062147                    False   
2      125.183137   125.292009      4  0.108872                    False   
7      165.036019   165.260244     12  0.224225                     True   
12     320.802130   321.031639     28  0.229509                    False   
13     339.458345   339.805143     32  0.346798                    False   
...           ...          ...    ...       ...                      ...   
2394  2034.655153  2034.765468    629  0.110315                    False   
2395  2043.892191  2044.079430    630  0.187238                    False   
2396  2045.095432  2045.393262    631  0.297830                     True   
2397  2051.142292  2051.269043    632  0.126751                     True   
2398  2053.276532  2053.445093    633  0.168561                    False   

          P_LR      P_RL    P_Long   P_Short  P_Long_LR  score_long_LR  \
0     0.771442  0.228558  0.639360  0.360640   0.493229       0.733209   
2     0.130706  0.869294  0.809296  0.190704   0.105780       0.896102   
7     0.549536  0.450464  0.693093  0.306907   0.380879       0.494846   
12    0.354534  0.645466  0.570362  0.429638   0.202213       0.426429   
13    0.501940  0.498060  0.413700  0.586300   0.207653       0.393133   
...        ...       ...       ...       ...        ...            ...   
2394  0.000316  0.999684  0.252939  0.747061   0.000080       0.708434   
2395  0.430877  0.569123  0.606759  0.393241   0.261439       0.592488   
2396  0.398701  0.601299  0.435845  0.564155   0.173772       0.369658   
2397  0.013759  0.986241  0.161866  0.838134   0.002227       0.608333   
2398  0.710155  0.289845  0.345384  0.654616   0.245276       0.604485   

      velocity_long_LR  intercept_long_LR  speed_long_LR  wcorr_long_LR  \
0           682.863416         167.051151     682.863416       0.577784   
2           195.502151          10.252852     195.502151       0.469147   
7           553.011642         178.641818     553.011642      -0.559428   
12         -209.846451         223.793273     209.846451      -0.584097   
13          -19.839717         218.528943      19.839717      -0.505325   
...                ...                ...            ...            ...   
2394       -183.184319         211.204525     183.184319      -0.449720   
2395        -98.459108          42.663808      98.459108      -0.648317   
2396          9.184061          24.204262       9.184061      -0.462515   
2397        735.918640         111.072891     735.918640       0.527320   
2398        691.310069          51.714159     691.310069       0.620141   

      pearsonr_long_LR  travel_long_LR  coverage_long_LR  jump_long_LR  \
0                  NaN        0.035694          0.262295      0.000156   
2                  NaN        0.053541          0.213115      0.000467   
7             0.634974        0.313597          0.393443      0.004439   
12            0.046008        0.428328          0.311475      0.004595   
13                 NaN        0.242422          0.262295      0.004283   
...                ...             ...               ...           ...   
2394               NaN        0.100438          0.258065      0.000613   
2395               NaN        0.153612          0.306452      0.003141   
2396               NaN        0.255231          0.354839      0.004443   
2397          0.696053        0.155089          0.354839      0.001302   
2398               NaN        0.166609          0.274194      0.001992   

      longest_sequence_length_ratio_long_LR  \
0                                  0.500000   
2                                  0.250000   
7                                  0.250000   
12                                 0.222222   
13                                 0.153846   
...                                     ...   
2394                               0.500000   
2395                               0.428571 

# Plotting via Plotly

In [22]:
import plotly.io as pio
template: str = 'plotly_dark' # set plotl template
# template: str = 'plotly_white'
pio.templates.default = template
from PIL import Image

from pyphocorehelpers.programming_helpers import copy_image_to_clipboard
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import _helper_build_figure, plotly_pre_post_delta_scatter, plot_across_sessions_scatter_results

# 1650, 446
fig_size_kwargs = {'width': 1650, 'height': 480}

In [23]:
concatenated_ripple_df = deepcopy(all_sessions_all_scores_ripple_df).infer_objects()

## Add plotly helper columns:
concatenated_ripple_df['pre_post_delta_category'] = 'post-delta'
concatenated_ripple_df['pre_post_delta_category'][concatenated_ripple_df['delta_aligned_start_t'] < 0.0] = 'pre-delta'


{'pre_post_delta_category': ['pre-delta', 'post-delta']
}

ripple_title_prefix = "User Annotated Sessions Ripples"

# concatenated_ripple_df = deepcopy(user_approved_ripple_df)
# ripple_title_prefix = "User Selected Ripples Only"

# concatenated_ripple_df = deepcopy(user_rejected_ripple_df)
# ripple_title_prefix = "User Rejected Ripples Only"

# concatenated_ripple_df = deepcopy(df)


# Create a bubble chart for ripples
enabled_time_bin_sizes = None
ripple_num_unique_sessions: int = concatenated_ripple_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
ripple_num_unique_time_bins: int = concatenated_ripple_df.time_bin_size.nunique(dropna=True)
ripple_title_string_suffix: str = f'{ripple_num_unique_sessions} Sessions'
ripple_title: str = f"{ripple_title_prefix} - {ripple_title_string_suffix}"
fig_ripples = _helper_build_figure(data_results_df=concatenated_ripple_df, histogram_bins=25, earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end, enabled_time_bin_sizes=enabled_time_bin_sizes, main_plot_mode='default', title=ripple_title)
fig_ripples.update_layout(fig_size_kwargs)
fig_ripples.show()
# fig_to_clipboard(fig_ripples)

num_unique_sessions: 9, num_unique_time_bins: 2
main_plot_mode: default
num_cols: 2


C:\Users\pho\AppData\Local\Temp\ipykernel_5920\2021887892.py:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  concatenated_ripple_df['pre_post_delta_category'][concatenated_ripple_df['delta_aligned_start_t'] < 0.0] = 'pre-delta'


In [24]:
histogram_bins = 25
# concatenated_ripple_df = deepcopy(df)

# ripple_title_prefix = 'test'
# # Create a bubble chart for ripples
# ripple_num_unique_sessions: int = concatenated_ripple_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
# # ripple_num_unique_time_bins: int = concatenated_ripple_df.time_bin_size.nunique(dropna=True)
# ripple_title_string_suffix: str = f'{ripple_num_unique_sessions} Sessions'
# ripple_title: str = f"{ripple_title_prefix} - {ripple_title_string_suffix}"
# fig_ripples = _helper_build_figure(data_results_df=concatenated_ripple_df, histogram_bins=histogram_bins, earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end, enabled_time_bin_sizes=None,
#                                     main_plot_mode='separate_row_per_session', title=ripple_title)

# concatenated_ripple_df = deepcopy(concatenated_ripple_df)
concatenated_ripple_df = deepcopy(all_sessions_all_scores_ripple_df)

# ['longest_sequence_length_ratio_diff', 'direction_change_bin_ratio_diff', 'congruent_dir_bins_ratio_diff', 'total_congruent_direction_change_diff']


# variable_name = 'P_Long'
variable_name = 'P_Short' # Shows expected effect - short-only replay prior to delta and then split replays post-delta
# variable_name = 'long_best_pf_peak_x_pearsonr'
# variable_name = 'long_best_jump'
# variable_name = 'wcorr_abs_diff'
# variable_name = 'pearsonr_abs_diff'
# variable_name = 'direction_change_bin_ratio_diff'
# variable_name = 'longest_sequence_length_ratio_diff'
# variable_name = 'long_best_longest_sequence_length_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'congruent_dir_bins_ratio_diff'
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
fig_ripples.update_layout(fig_size_kwargs)

_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')

# fig_to_clipboard(new_fig_ripples, **fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 9, num_unique_time_bins: 2
len(pre_delta_fig.data): 2


In [25]:
# new_fig_ripples.get_subplot(
# import kaleido

# new_fig_ripples.layout
new_fig_ripples.layout.width

# from kaleido._version import __version__ # '0.1.0.post1'
# __version__

color_options = ["is_user_annotated_epoch", "pre_post_delta_category"]

variable_options = {'pre_post_delta_category': ['pre-delta', 'post-delta']
}

concatenated_ripple_df

start         stop  label  duration  is_user_annotated_epoch  \
0        5.696837     5.758983      0  0.062147                    False   
1       27.174099    27.439336      1  0.265236                    False   
2       96.866562    97.257596      2  0.391035                    False   
3      121.201428   121.606901      3  0.405473                    False   
4      125.183137   125.292009      4  0.108872                    False   
...           ...          ...    ...       ...                      ...   
3861  2034.655153  2034.765468    629  0.110315                    False   
3862  2043.892191  2044.079430    630  0.187238                    False   
3863  2045.095432  2045.393262    631  0.297830                     True   
3864  2051.142292  2051.269043    632  0.126751                     True   
3865  2053.276532  2053.445093    633  0.168561                    False   

      is_valid_epoch      P_LR      P_RL    P_Long   P_Short  P_Long_LR  \
0               True  0.771442  0.228558  0.639360  0.360640   0.493229   
1              False  0.510945  0.489055  0.495263  0.504737   0.253052   
2               True  0.380731  0.619269  0.543552  0.456448   0.206947   
3              False  0.316117  0.683883  0.495285  0.504715   0.156568   
4               True  0.130706  0.869294  0.809296  0.190704   0.105780   
...              ...       ...       ...       ...       ...        ...   
3861            True  0.000316  0.999684  0.252939  0.747061   0.000080   
3862            True  0.430877  0.569123  0.606759  0.393241   0.261439   
3863            True  0.398701  0.601299  0.435845  0.564155   0.173772   
3864            True  0.013759  0.986241  0.161866  0.838134   0.002227   
3865            True  0.710155  0.289845  0.345384  0.654616   0.245276   

      score_long_LR  velocity_long_LR  intercept_long_LR  speed_long_LR  \
0          0.733209        682.863416         167.051151     682.863416   
1          0.338389         23.582867         182.711950      23.582867   
2          0.379806         11.124767         214.173480      11.124767   
3          0.473496         -5.215588          18.683737       5.215588   
4          0.896102        195.502151          10.252852     195.502151   
...             ...               ...                ...            ...   
3861       0.708434       -183.184319         211.204525     183.184319   
3862       0.592488        -98.459108          42.663808      98.459108   
3863       0.369658          9.184061          24.204262       9.184061   
3864       0.608333        735.918640         111.072891     735.918640   
3865       0.604485        691.310069          51.714159     691.310069   

      wcorr_long_LR  pearsonr_long_LR  travel_long_LR  coverage_long_LR  \
0          0.577784               NaN        0.035694          0.262295   
1          0.074217               NaN        0.186402          0.311475   
2          0.126189          0.254583        0.160623          0.426230   
3          0.104757               NaN        0.425949          0.311475   
4          0.469147               NaN        0.053541          0.213115   
...             ...               ...             ...               ...   
3861      -0.449720               NaN        0.100438          0.258065   
3862      -0.648317               NaN        0.153612          0.306452   
3863      -0.462515               NaN        0.255231          0.354839   
3864       0.527320          0.696053        0.155089          0.354839   
3865       0.620141               NaN        0.166609          0.274194   

      jump_long_LR  longest_sequence_length_ratio_long_LR  \
0         0.000156                               0.500000   
1         0.002025                               0.200000   
2         0.004128                               0.133333   
3         0.004673                               0.125000   
4         0.000467                               0.250000   
...            ...            

In [27]:
variable_name = 'short_best_direction_change_bin_ratio'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'short_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"pre_post_delta_category", 'title': f"'{variable_name}'"} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], , 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="pre_post_delta_category") # , histnorm='probability density'
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

num_unique_sessions: 9, num_unique_time_bins: 2
len(pre_delta_fig.data): 1


In [28]:
# variable_name = 'total_congruent_direction_change_diff'
# variable_name = 'long_best_congruent_dir_bins_ratio'
# variable_name = 'long_best_total_congruent_direction_change'
variable_name = 'wcorr_diff'
# variable_name = 'long_best_wcorr'
# 'color':'is_user_annotated_epoch'
# 'color': 'is_user_annotated_epoch', 
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'color':"is_user_annotated_epoch", 'title': f"'{variable_name}'", 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size', 'is_user_annotated_epoch':'user_sel'}} # , 'color': 'time_bin_size', 'range_y': [-1.0, 1.0], 
# hist_kwargs = dict(color="time_bin_size")
hist_kwargs = dict(color="is_user_annotated_epoch") # , histnorm='probability density'
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=concatenated_ripple_df, out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, hist_kwargs=hist_kwargs, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict = {}
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.0, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 9, num_unique_time_bins: 2
len(pre_delta_fig.data): 2


## Stats Tests

In [29]:
from pyphocorehelpers.indexing_helpers import partition, partition_df, partition_df_dict
import scipy.stats as stats

# stats_variable_name: str = 'P_Short'
# stats_variable_name: str = 'short_best_direction_change_bin_ratio'
stats_variable_name: str = 'short_best_wcorr'

## INPUTS: stats_variable_name, valid_ripple_df


# ['pre-delta', 'post-delta']
analysis_df = deepcopy(valid_ripple_df[["delta_aligned_start_t", "pre_post_delta_category", stats_variable_name]]).dropna(subset=["pre_post_delta_category", stats_variable_name])
# partition_df(analysis_df, partitionColumn='pre_post_delta_category')

# _partition_values, (_pre_delta_df, _post_delta_df) = partition(analysis_df, partitionColumn='pre_post_delta_category') # use `valid_ripple_df` instead of the original dataframe to only get those which are valid.
_pre_post_delta_partition_df_dict = partition_df_dict(analysis_df, partitionColumn='pre_post_delta_category')
_pre_delta_df = _pre_post_delta_partition_df_dict['pre-delta']
_post_delta_df = _pre_post_delta_partition_df_dict['post-delta']

actual_diff_means = np.nanmean(_post_delta_df[stats_variable_name].to_numpy()) - np.nanmean(_pre_delta_df[stats_variable_name].to_numpy())
print(f'stats_variable_name: {stats_variable_name}: actual_diff_means: {actual_diff_means}')

_pre_delta_df
_post_delta_df

stats_variable_name: short_best_wcorr: actual_diff_means: -0.05136739076830328


delta_aligned_start_t pre_post_delta_category  short_best_wcorr
30                26.946180              post-delta         -0.012402
31                29.325473              post-delta          0.083639
32                30.670886              post-delta          0.237903
33                37.628931              post-delta         -0.130230
34                38.445131              post-delta         -0.114506
...                     ...                     ...               ...
2394             823.097073              post-delta         -0.276354
2395             832.334111              post-delta         -0.570605
2396             833.537352              post-delta         -0.320426
2397             839.584212              post-delta          0.332299
2398             841.718452              post-delta          0.770480

[1282 rows x 3 columns]

In [30]:
n_shuffles: int = 10000
# stats_variable_name: str = 'P_Short'

shuffle_results = []
## INPUT: n_shuffles, analysis_df, stats_variable_name
shuffled_analysis_df = deepcopy(analysis_df)
for i in np.arange(n_shuffles):
    # shuffled_analysis_df[stats_variable_name] = shuffled_analysis_df[stats_variable_name].sample(frac=1).to_numpy() # .reset_index(drop=True)
    shuffled_analysis_df['pre_post_delta_category'] = shuffled_analysis_df.sample(frac=1)['pre_post_delta_category'].to_numpy()
    _shuffled_pre_post_delta_partition_df_dict = partition_df_dict(shuffled_analysis_df, partitionColumn='pre_post_delta_category')
    _shuffled_pre_delta_df = _shuffled_pre_post_delta_partition_df_dict['pre-delta']
    _shuffled_post_delta_df = _shuffled_pre_post_delta_partition_df_dict['post-delta']

    _diff_mean = np.nanmean(_shuffled_post_delta_df[stats_variable_name].to_numpy()) - np.nanmean(_shuffled_pre_delta_df[stats_variable_name].to_numpy())
    shuffle_results.append(_diff_mean)

shuffle_results = np.array(shuffle_results)
shuffle_results

array([ 0.01274918, -0.01188322,  0.01073624, ..., -0.00907053,
       -0.00381518,  0.02164291])

In [ ]:
np.sum(actual_diff_means > np.abs(shuffle_results))

In [31]:
# Create the data for two groups
# group1 = np.random.rand(25)
# group2 = np.random.rand(20)

## INPUTS: stats_variable_name
print(f'stats_variable_name: {stats_variable_name}')

group1 = _pre_delta_df[stats_variable_name].to_numpy()
group2 = _post_delta_df[stats_variable_name].to_numpy()

# perform mann whitney test 
stat, p_value = stats.mannwhitneyu(group1, group2) 
print('Statistics=%.2f, p=%.2f' % (stat, p_value)) 

# Level of significance 
alpha = 0.05
# conclusion 
if p_value < alpha: 
    print('Reject Null Hypothesis (Significant difference between two samples)') 
else: 
    print('Do not Reject Null Hypothesis (No significant difference between two samples)')

# Calculate the sample variances
variance1 = np.var(group1, ddof=1)
variance2 = np.var(group2, ddof=1)
 
print('Variance 1:',variance1)
print('Variance 2:',variance2)

# Calculate the F-statistic
f_value = variance1 / variance2
 
# Calculate the degrees of freedom
df1 = len(group1) - 1
df2 = len(group2) - 1
 
# Calculate the p-value
p_value = stats.f.cdf(f_value, df1, df2)
 
# Print the results
print('Degree of freedom 1:',df1)
print('Degree of freedom 2:',df2)
print("F-statistic:", f_value)
print("p-value:", p_value)


# Statistics=351933.00, p=0.00
# Reject Null Hypothesis (Significant difference between two samples)
# Variance 1: 0.017720245875104713
# Variance 2: 0.02501347759017487
# Degree of freedom 1: 1104
# Degree of freedom 2: 1282
# F-statistic: 0.7084279189577826
# p-value: 1.882791591520268e-09


# stats_variable_name: short_best_wcorr
# Statistics=770405.00, p=0.00
# Reject Null Hypothesis (Significant difference between two samples)
# Variance 1: 0.13962063046395118
# Variance 2: 0.15575146845969287
# Degree of freedom 1: 1108
# Degree of freedom 2: 1281
# F-statistic: 0.8964321931904211
# p-value: 0.030077963036698012

stats_variable_name: short_best_wcorr
Statistics=769814.00, p=0.00
Reject Null Hypothesis (Significant difference between two samples)
Variance 1: 0.13718152404059009
Variance 2: 0.150539412574384
Degree of freedom 1: 1108
Degree of freedom 2: 1281
F-statistic: 0.9112665028688514
p-value: 0.055055302694622485


In [32]:
## User non-selected:
scatter_title = f'user_approved_ripple_df Sevveral Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_approved_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
_extras_output_dict["y_mid_line"] = new_fig_ripples.add_hline(y=0.5, line=dict(color="rgba(0.8,0.8,0.8,.75)", width=2), row='all', col='all')
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples

num_unique_sessions: 9, num_unique_time_bins: 2
len(pre_delta_fig.data): 1


In [ ]:
# IDEA: The ones with clear replays (diagonal sequences in the decoded posteriors) are by definiition ambiguous, because there's not much difference between the long/short decoders.


In [33]:
## User non-selected:
scatter_title = f'Non-selected Sevveral Sessions {variable_name}'
# variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} # , 'color': 'time_bin_size'
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=deepcopy(user_rejected_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


NameError: name 'user_rejected_ripple_df' is not defined

In [34]:
# Laps test
concatenated_ripple_df = deepcopy(all_sessions_simple_pearson_laps_df)

scatter_title = 'Sevveral Sessions'
variable_name = 'wcorr_abs_diff'
px_scatter_kwargs = {'x': 'delta_aligned_start_t', 'y': variable_name, 'title': scatter_title, 'range_y': [0.0, 1.0], 'labels': {'session_name': 'Session', 'time_bin_size': 'tbin_size'}} 
new_fig_ripples = plotly_pre_post_delta_scatter(data_results_df=deepcopy(concatenated_ripple_df), out_scatter_fig=None, histogram_bins=histogram_bins,
                        px_scatter_kwargs=px_scatter_kwargs, histogram_variable_name=variable_name, forced_range_y=None,
                        time_delta_tuple=(earliest_delta_aligned_t_start, 0.0, latest_delta_aligned_t_end))
new_fig_ripples.update_layout(fig_size_kwargs)
new_fig_ripples


num_unique_sessions: 12, num_unique_time_bins: 2
len(pre_delta_fig.data): 1


# Plotting functions

In [35]:
from pyphoplacecellanalysis.General.Model.Configs.LongShortDisplayConfig import PlottingHelpers
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import plot_across_sessions_scatter_results

# Example usage:
all_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_df, concatenated_ripple_df=all_sessions_ripple_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   laps_title_prefix=f"Laps", ripple_title_prefix=f"Ripples", save_figures=True, figure_save_extension=['.html','.png'])
fig_laps, fig_ripples = all_session_figures[0]
# fig_laps.update_layout(fig_size_kwargs)
# fig_ripples.update_layout(fig_size_kwargs)

# fig_laps.show()
fig_ripples.show()
# fig_laps.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_laps.html")
# fig_ripples.write_html(f"../output/{TODAY_DAY_DATE}_AcrossSession_fig_ripples.html")

plot_across_sessions_results(directory: K:\scratch\collected_outputs)
	figures_folder: file:///K:/scratch/collected_outputs/figures
num_unique_sessions: 13, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
num_unique_sessions: 13, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
	saving figures...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_laps_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_ripples_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_laps_marginal.png"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_ripples_marginal.png"...


In [ ]:
fig_to_clipboard(fig_ripples)

In [36]:
## time_bin version:
all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='separate_row_per_session',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=True, figure_save_extension=['.html','.png'])
fig_time_bin_laps, fig_time_bin_ripples = all_time_bin_session_figures[0]
# fig_time_bin_laps.show()
fig_time_bin_ripples.show()

plot_across_sessions_results(directory: K:\scratch\collected_outputs)
	figures_folder: file:///K:/scratch/collected_outputs/figures
num_unique_sessions: 13, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
num_unique_sessions: 13, num_unique_time_bins: 1
main_plot_mode: separate_row_per_session
	saving figures...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_laps_per_time_bin_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_ripples_per_time_bin_marginal.html"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_laps_per_time_bin_marginal.png"...
	saving "file:///K:/scratch/collected_outputs/figures/13-Sessions_ripples_per_time_bin_marginal.png"...


In [37]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import plot_across_sessions_scatter_results, _helper_build_figure

## Test collapsed histograms-only results:
histograms_only_all_time_bin_session_figures = plot_across_sessions_scatter_results(collected_outputs_directory, concatenated_laps_df=all_sessions_laps_time_bin_df, concatenated_ripple_df=all_sessions_ripple_time_bin_df,
														#    enabled_time_bin_sizes=[0.03, 0.10],
															# enabled_time_bin_sizes=[0.03, 0.058, 0.10], # [0.03 , 0.044, 0.058, 0.072, 0.086, 0.1]
														   earliest_delta_aligned_t_start=earliest_delta_aligned_t_start, latest_delta_aligned_t_end=latest_delta_aligned_t_end,
														   main_plot_mode='default',
														   laps_title_prefix=f"Laps_per_time_bin", ripple_title_prefix=f"Ripples_per_time_bin", save_figures=False, figure_save_extension=['.html','.png'])
histograms_only_fig_time_bin_laps, histograms_only_fig_time_bin_ripples = histograms_only_all_time_bin_session_figures[0]
# histograms_only_fig_time_bin_laps.show()
histograms_only_fig_time_bin_ripples.show()

ImportError: cannot import name 'plot_across_sessions_scatter_results' from 'pyphoplacecellanalysis.SpecificResults.PendingNotebookCode' (C:\Users\pho\repos\Spike3DWorkEnv\pyPhoPlaceCellAnalysis\src\pyphoplacecellanalysis\SpecificResults\PendingNotebookCode.py)

In [ ]:
import plotly.subplots as sp
import plotly.graph_objs as go

from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import plotly_pre_post_delta_scatter
# data_results_df: pd.DataFrame = deepcopy(all_sessions_laps_df) # all_sessions_laps_time_bin_df
# histogram_bins = 'auto'
histogram_bins: int = 25

new_laps_fig = plotly_pre_post_delta_scatter(data_results_df=deepcopy(all_sessions_laps_df), out_scatter_fig=fig_laps, histogram_bins=histogram_bins)
new_laps_fig

# Matplotlib-based versions:

In [ ]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import plot_histograms

matplotlib.use('Qt5Agg')

In [ ]:
# from Spike3D.PendingNotebookCode import plot_stacked_histograms

# You can use it like this:'long_best_dir_simple_pearsonr'
_out0: "MatplotlibRenderPlots" = plot_histograms(all_sessions_laps_time_bin_df, 'Laps', 'All Sessions', "75 ms")
_out1: "MatplotlibRenderPlots" = plot_histograms(all_sessions_ripple_time_bin_df, 'Ripples', 'All Sessions', "75 ms")

In [ ]:


fig_to_clipboard(_out0.figures[0])

In [ ]:
## all_sessions_new_laps_df, all_sessions_new_ripple_df
plot_histograms(all_sessions_new_laps_df, 'New Laps', 'All Sessions', "25 ms")
plot_histograms(all_sessions_new_ripple_df, 'New Ripples', 'All Sessions', "25 ms")


In [ ]:
all_sessions_new_laps_df

In [ ]:
len(all_sessions_new_laps_df['session_name'].unique()) # 10 sessions



In [ ]:
from pyphoplacecellanalysis.SpecificResults.PendingNotebookCode import plot_stacked_histograms

# You can use it like this:
num_unique_sessions: int = all_sessions_laps_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_laps_time_bin_df.time_bin_size.nunique(dropna=True)
plot_stacked_histograms(all_sessions_laps_time_bin_df, 'Laps', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes")

num_unique_sessions: int = all_sessions_ripple_time_bin_df.session_name.nunique(dropna=True) # number of unique sessions, ignoring the NA entries
num_unique_time_bins: int = all_sessions_ripple_time_bin_df.time_bin_size.nunique(dropna=True)
plot_stacked_histograms(all_sessions_ripple_time_bin_df, 'Ripples', f'{num_unique_sessions} Sessions', f"{num_unique_time_bins} tbin sizes")

# 2024-03-28 - AcrossSessionTable (PhoDibaPaper2023 formats) .h5 and figure exports

In [40]:
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionTables
from pyphoplacecellanalysis.SpecificResults.AcrossSessionResults import AcrossSessionsVisualizations

neuron_identities_table, long_short_fr_indicies_analysis_table, neuron_replay_stats_table = AcrossSessionTables.build_all_known_tables(included_session_contexts, included_h5_paths, should_restore_native_column_types=True)
# matplotlib_configuration_update(is_interactive=True, backend='Qt5Agg')
matplotlib.use('Qt5Agg')
graphics_output_dict = AcrossSessionsVisualizations.across_sessions_firing_rate_index_figure(long_short_fr_indicies_analysis_results=long_short_fr_indicies_analysis_table, num_sessions=num_sessions)

failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-08_14-26-15_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-08_14-26-15/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-08_14-26-15/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-09_1-22-43_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-09_1-22-43/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-09_1-22-43/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006-6-12_15-55-31_pipeline_results.h5, table_key: /kdiba/gor01/one/2006-6-12_15-55-31/neuron_identities/table. wth exception group ``/`` does not have a child named ``/kdiba/gor01/one/2006-6-12_15-55-31/neuron_identities/table``. Skipping.
failed for file path: K:\scratch\collected_outputs\2024-03-28_Apogee_2006

C:\Users\pho\AppData\Local\Temp\ipykernel_5920\1377923007.py:6: MatplotlibDeprecationWarning:

Auto-close()ing of figures upon backend switching is deprecated since 3.8 and will be removed two minor releases later.  To suppress this warning, explicitly call plt.close('all') first.

